In [0]:
import pandas as pd
import numpy as np
import pickle
import matplotlib.pyplot as plt
from scipy import stats
import tensorflow as tf
import seaborn as sns
from pylab import rcParams
from sklearn import metrics
from sklearn.model_selection import train_test_split
from tensorflow.python.framework import ops
from google.colab import drive 


sns.set(style='whitegrid', palette='muted', font_scale=1.5)

RANDOM_SEED = 42

In [0]:
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
#Load Data
columns = ['activity', 'x-axis', 'y-axis', 'z-axis']
df = pd.read_csv('gdrive/My Drive/MC_Project/data.csv', header = None, names = columns)
df = df.dropna()

In [0]:
#Preprocessing
STEPS = 200

N_FEATURES = 3
stepcount = 20
features = []
labels = []
for i in range(0, len(df) - STEPS, stepcount):
    x = df['x-axis'].values[i: i + STEPS]
    y = df['y-axis'].values[i: i + STEPS]
    z = df['z-axis'].values[i: i + STEPS]
    label = stats.mode(df['activity'][i: i + STEPS])[0][0]
    features.append([x, y, z])
    labels.append(label)

In [0]:
#Reshape
new_features = np.asarray(features, dtype= np.float32).reshape(-1, STEPS, N_FEATURES)
labels = np.asarray(pd.get_dummies(labels), dtype = np.float32)


In [0]:
X_train, X_test, y_train, y_test = train_test_split(
        new_features, labels, test_size=0.2, random_state=RANDOM_SEED)


In [0]:
#LSTM Model
N_CLASSES = 5
N_HIDDEN_UNITS = 64

def create_LSTM_model(inputs):
    W = {
        'hidden': tf.Variable(tf.random_normal([N_FEATURES, N_HIDDEN_UNITS])),
        'output': tf.Variable(tf.random_normal([N_HIDDEN_UNITS, N_CLASSES]))
    }
    biases = {
        'hidden': tf.Variable(tf.random_normal([N_HIDDEN_UNITS], mean=1.0)),
        'output': tf.Variable(tf.random_normal([N_CLASSES]))
    }
    
    X = tf.transpose(inputs, [1, 0, 2])
    X = tf.reshape(X, [-1, N_FEATURES])
    hidden = tf.nn.relu(tf.matmul(X, W['hidden']) + biases['hidden'])
    hidden = tf.split(hidden, STEPS, 0)

    # 2 layers of LSTM after tuning
    lstm_layers = [tf.contrib.rnn.BasicLSTMCell(N_HIDDEN_UNITS, forget_bias=1.0) for layer in range(2)]
    lstm_layers = tf.contrib.rnn.MultiRNNCell(lstm_layers)

    outputs, _ = tf.contrib.rnn.static_rnn(lstm_layers, hidden, dtype=tf.float32)

    # Get output for the last time step
    lstm_last_output = outputs[-1]

    return tf.matmul(lstm_last_output, W['output']) + biases['output']

In [0]:
tf.reset_default_graph()

X = tf.placeholder(tf.float32, [None, STEPS, N_FEATURES], name="input")
Y = tf.placeholder(tf.float32, [None, N_CLASSES])

In [0]:
pred_Y = create_LSTM_model(X)

pred_softmax = tf.nn.softmax(pred_Y, name="y_")

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
This class is equivalent as tf.keras.layers.StackedRNNCells, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell, unroll=True)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [0]:
l2 = 0.002 * \
    sum(tf.nn.l2_loss(tf_var) for tf_var in tf.trainable_variables())

loss = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits = pred_Y, labels = Y)) + l2

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [0]:
optimizer = tf.train.AdamOptimizer(learning_rate=0.002).minimize(loss)

correct_pred = tf.equal(tf.argmax(pred_softmax, 1), tf.argmax(Y, 1))
accuracy = tf.reduce_mean(tf.cast(correct_pred, dtype=tf.float32))

In [0]:
N_EPOCHS = 50
BATCH_SIZE = 1024

In [0]:
saver = tf.train.Saver()

history = dict(train_loss=[], 
                     train_acc=[], 
                     test_loss=[], 
                     test_acc=[])

sess=tf.InteractiveSession()
sess.run(tf.global_variables_initializer())

train_count = len(X_train)

for i in range(1, N_EPOCHS + 1):
    for start, end in zip(range(0, train_count, BATCH_SIZE),
                          range(BATCH_SIZE, train_count + 1,BATCH_SIZE)):
        sess.run(optimizer, feed_dict={X: X_train[start:end],
                                       Y: y_train[start:end]})

    _, acc_train, loss_train = sess.run([pred_softmax, accuracy, loss], feed_dict={
                                            X: X_train, Y: y_train})

    _, acc_test, loss_test = sess.run([pred_softmax, accuracy, loss], feed_dict={
                                            X: X_test, Y: y_test})

    history['train_loss'].append(loss_train)
    history['train_acc'].append(acc_train)
    history['test_loss'].append(loss_test)
    history['test_acc'].append(acc_test)

    if i != 1 and i % 10 != 0:
        continue

    print(f'epoch: {i} test accuracy: {acc_test} loss: {loss_test}')
    
predictions, acc_final, loss_final = sess.run([pred_softmax, accuracy, loss], feed_dict={X: X_test, Y: y_test})

epoch: 1 test accuracy: 0.8444586396217346 loss: 1.319022536277771
epoch: 10 test accuracy: 0.9593843817710876 loss: 0.65076744556427
epoch: 20 test accuracy: 0.9686731696128845 loss: 0.4503941237926483
epoch: 30 test accuracy: 0.981422483921051 loss: 0.3177414536476135
epoch: 40 test accuracy: 0.9845187067985535 loss: 0.2587294578552246
epoch: 50 test accuracy: 0.9863400459289551 loss: 0.21867018938064575


In [0]:
pickle.dump(predictions, open("gdrive/My Drive/MC_Project/predictions.p", "wb"))
pickle.dump(history, open("gdrive/My Drive/MC_Project//history.p", "wb"))
tf.train.write_graph(sess.graph_def, '.', 'gdrive/My Drive/MC_Project/har.pbtxt')  
saver.save(sess, save_path = "gdrive/My Drive/MC_Project/har.ckpt")
sess.close()

In [0]:
history = pickle.load(open("gdrive/My Drive/MC_Project/history.p", "rb"))
predictions = pickle.load(open("gdrive/My Drive/MC_Project/predictions.p", "rb"))

In [0]:
LABELS = ['Push-up', 'Running', 'Sitting', 'Standing', 'Walking']

max_test = np.argmax(y_test, axis=1)
max_predictions = np.argmax(predictions, axis=1)
confusion_matrix = metrics.confusion_matrix(max_test, max_predictions)


In [0]:
confusion_matrix

array([[2244,   10,    2,    0,    9],
       [  39, 3400,    1,    0,    7],
       [   4,    0,  569,    3,    1],
       [   6,    0,    5,  425,    1],
       [  55,    6,    1,    0, 4193]])

In [0]:
from tensorflow.python.tools import freeze_graph

MODEL_NAME = 'har'

input_graph_path = 'gdrive/My Drive/MC_Project/' + MODEL_NAME+'.pbtxt'
checkpoint_path = 'gdrive/My Drive/MC_Project/' +MODEL_NAME+'.ckpt'
restore_op_name = "save/restore_all"
filename_tensor_name = "save/Const:0"
output_frozen_graph_name = 'gdrive/My Drive/MC_Project/frozen_'+MODEL_NAME+'.pb'

freeze_graph.freeze_graph(input_graph_path, input_saver="",
                          input_binary=False, input_checkpoint=checkpoint_path, 
                          output_node_names="y_", restore_op_name="save/restore_all",
                          filename_tensor_name="save/Const:0", 
                          output_graph=output_frozen_graph_name, clear_devices=True, initializer_nodes="")

Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from gdrive/My Drive/MC_Project/har.ckpt
Instructions for updating:
Use `tf.compat.v1.graph_util.convert_variables_to_constants`
Instructions for updating:
Use `tf.compat.v1.graph_util.extract_sub_graph`
INFO:tensorflow:Froze 8 variables.
INFO:tensorflow:Converted 8 variables to const ops.


node {
  name: "input"
  op: "Placeholder"
  attr {
    key: "dtype"
    value {
      type: DT_FLOAT
    }
  }
  attr {
    key: "shape"
    value {
      shape {
        dim {
          size: -1
        }
        dim {
          size: 200
        }
        dim {
          size: 3
        }
      }
    }
  }
}
node {
  name: "Variable"
  op: "Const"
  attr {
    key: "dtype"
    value {
      type: DT_FLOAT
    }
  }
  attr {
    key: "value"
    value {
      tensor {
        dtype: DT_FLOAT
        tensor_shape {
          dim {
            size: 3
          }
          dim {
            size: 64
          }
        }
        tensor_content: ")\221g>mQ\213\277\366\207\035\276yr\227=\343\220\232\276W\001\330=\025\364i\275\3322l\277\344F[>[\306\313?\310\352\311>\341\314\036?\337S\311\276{\312Y\277\000\321\016?\031\326\250\274\341\211\234\2762T.\277y\177\221?-\271;\277B\016\215\275\212;B\275\342*\322\275g\315\266>P\343o\2762\266\263=3x\207?\327\221O\277&\214\274>\262\230D\277O\361S\276